In [1]:
# IP USED THROUGHOUT THE ASSIGNMENT
hostip = "172.22.32.1"

In [ ]:
import time
from datetime import datetime
from pymongo import MongoClient
from kafka3 import KafkaProducer
import json
from bson.json_util import dumps
from kafka3.admin import KafkaAdminClient, NewTopic
import time

def recreate_topics(bootstrap_servers:str, topics:str,
                    num_partitions:int=1, replication_factor:int=1):
    """
    This function are created to help purge Kafka producer streams we just created to
    
    """
    # Ensure we pass a list of host:port strings
    if isinstance(bootstrap_servers, str):
        bs_list = [bootstrap_servers]
    else:
        bs_list = bootstrap_servers

    admin = KafkaAdminClient(bootstrap_servers=bs_list)
    try:
        admin.delete_topics(topics)
        print(f"[INFO] Deletion of topics {topics} initiated.")
    except Exception as e:
        print(f"[WARN] Could not delete topics: {e}")
    finally:
        admin.close()


# Kafka setup
topic = "mongo_plot_stream"
kafka_server = f"{hostip}:9092"

# PURGE & RECREATE before producing
recreate_topics(kafka_server, [topic],
                num_partitions=1,
                replication_factor=1)

# ── Setup ──
mongo_client = MongoClient(f"mongodb://{hostip}:27017")
db           = mongo_client["fit3182_db"]
collection   = db["Violation"]

producer = KafkaProducer(
    bootstrap_servers=kafka_server,            # your Kafka broker
    value_serializer=lambda v: dumps(v).encode('utf-8')
)
stream_topic = topic

# ── Initialize cursor at 2024-01-01T00:00:00Z ──
last_ts = datetime(2024, 1, 1)

try:
    while True:
        # find any document with at least one new violation
        query = {"violations.timestamp_start": {"$gt": last_ts}}
        # sort by the embedded timestamp so you process older docs first
        new_docs = list(collection
                        .find(query)
                        .sort("violations.timestamp_start", 1))

        for doc in new_docs:
            # send the full document, preserving original structure
            producer.send(stream_topic, doc)
            print(f"✅ Sent to Kafka ({stream_topic}): {doc}")

            # bump last_ts to the newest violation in this doc
            timestamps = [v["timestamp_start"] for v in doc["violations"]]
            max_ts = min(timestamps)
            if max_ts > last_ts:
                last_ts = max_ts

        producer.flush()
        time.sleep(3)

except KeyboardInterrupt:
    print("Stopped by user")

finally:
    producer.close()

[INFO] Deletion of topics ['mongo_plot_stream'] initiated.
✅ Sent to Kafka (mongo_plot_stream): {'_id': ObjectId('6836db18c81318e00db494f9'), 'car_plate': 'KKE 15', 'date': datetime.datetime(2024, 1, 1, 0, 0), 'violations': [{'violation_id': '9fa3dac3-a503-43fc-8a3d-fc3605de91cc', 'type': 'instantaneous', 'camera_id_start': 1, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 8, 0), 'timestamp_end': None, 'measured_speed': 150.3}, {'violation_id': '53ed0e03-c804-4d5c-97eb-b24409dc1bcf', 'type': 'instantaneous', 'camera_id_start': 2, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 8, 0, 23, 896000), 'timestamp_end': None, 'measured_speed': 138.3}, {'violation_id': 'ae45bf16-62d7-495b-ad4a-dfc321e4969f', 'type': 'average', 'camera_id_start': 1, 'camera_id_end': 2, 'timestamp_start': datetime.datetime(2024, 1, 1, 8, 0), 'timestamp_end': datetime.datetime(2024, 1, 1, 8, 0, 23, 896000), 'measured_speed': 144.3}, {'violation_id': '910d3957-2329-4

✅ Sent to Kafka (mongo_plot_stream): {'_id': ObjectId('6836dcccc81318e00db49781'), 'car_plate': 'ZKP 560', 'date': datetime.datetime(2024, 1, 1, 0, 0), 'violations': [{'violation_id': '7e30e21c-152a-4552-9acb-93971451906a', 'type': 'instantaneous', 'camera_id_start': 1, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 24, 48), 'timestamp_end': None, 'measured_speed': 156.1}, {'violation_id': 'fcb618ab-3dd2-421d-a705-f90e82c3f2b3', 'type': 'instantaneous', 'camera_id_start': 2, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 25, 12, 218000), 'timestamp_end': None, 'measured_speed': 159.2}, {'violation_id': '2fbfc4da-64a0-4e5e-9edd-dd84091be7b3', 'type': 'average', 'camera_id_start': 1, 'camera_id_end': 2, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 24, 48), 'timestamp_end': datetime.datetime(2024, 1, 1, 9, 25, 12, 218000), 'measured_speed': 157.64999999999998}, {'violation_id': '4cddb310-14f7-4b86-8b18-f609248136d5', 'type': '

✅ Sent to Kafka (mongo_plot_stream): {'_id': ObjectId('6836dcccc81318e00db49781'), 'car_plate': 'ZKP 560', 'date': datetime.datetime(2024, 1, 1, 0, 0), 'violations': [{'violation_id': '7e30e21c-152a-4552-9acb-93971451906a', 'type': 'instantaneous', 'camera_id_start': 1, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 24, 48), 'timestamp_end': None, 'measured_speed': 156.1}, {'violation_id': 'fcb618ab-3dd2-421d-a705-f90e82c3f2b3', 'type': 'instantaneous', 'camera_id_start': 2, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 25, 12, 218000), 'timestamp_end': None, 'measured_speed': 159.2}, {'violation_id': '2fbfc4da-64a0-4e5e-9edd-dd84091be7b3', 'type': 'average', 'camera_id_start': 1, 'camera_id_end': 2, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 24, 48), 'timestamp_end': datetime.datetime(2024, 1, 1, 9, 25, 12, 218000), 'measured_speed': 157.64999999999998}, {'violation_id': '4cddb310-14f7-4b86-8b18-f609248136d5', 'type': '

✅ Sent to Kafka (mongo_plot_stream): {'_id': ObjectId('6836dcccc81318e00db49781'), 'car_plate': 'ZKP 560', 'date': datetime.datetime(2024, 1, 1, 0, 0), 'violations': [{'violation_id': '7e30e21c-152a-4552-9acb-93971451906a', 'type': 'instantaneous', 'camera_id_start': 1, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 24, 48), 'timestamp_end': None, 'measured_speed': 156.1}, {'violation_id': 'fcb618ab-3dd2-421d-a705-f90e82c3f2b3', 'type': 'instantaneous', 'camera_id_start': 2, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 25, 12, 218000), 'timestamp_end': None, 'measured_speed': 159.2}, {'violation_id': '2fbfc4da-64a0-4e5e-9edd-dd84091be7b3', 'type': 'average', 'camera_id_start': 1, 'camera_id_end': 2, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 24, 48), 'timestamp_end': datetime.datetime(2024, 1, 1, 9, 25, 12, 218000), 'measured_speed': 157.64999999999998}, {'violation_id': '4cddb310-14f7-4b86-8b18-f609248136d5', 'type': '

✅ Sent to Kafka (mongo_plot_stream): {'_id': ObjectId('6836dcccc81318e00db49781'), 'car_plate': 'ZKP 560', 'date': datetime.datetime(2024, 1, 1, 0, 0), 'violations': [{'violation_id': '7e30e21c-152a-4552-9acb-93971451906a', 'type': 'instantaneous', 'camera_id_start': 1, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 24, 48), 'timestamp_end': None, 'measured_speed': 156.1}, {'violation_id': 'fcb618ab-3dd2-421d-a705-f90e82c3f2b3', 'type': 'instantaneous', 'camera_id_start': 2, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 25, 12, 218000), 'timestamp_end': None, 'measured_speed': 159.2}, {'violation_id': '2fbfc4da-64a0-4e5e-9edd-dd84091be7b3', 'type': 'average', 'camera_id_start': 1, 'camera_id_end': 2, 'timestamp_start': datetime.datetime(2024, 1, 1, 9, 24, 48), 'timestamp_end': datetime.datetime(2024, 1, 1, 9, 25, 12, 218000), 'measured_speed': 157.64999999999998}, {'violation_id': '4cddb310-14f7-4b86-8b18-f609248136d5', 'type': '

...

✅ Sent to Kafka (mongo_plot_stream): {'_id': ObjectId('6836ed8cc81318e00db4b428'), 'car_plate': 'SI 61', 'date': datetime.datetime(2024, 1, 1, 0, 0), 'violations': [{'violation_id': 'f1eb0747-85bf-4637-a31f-a02d1496ae82', 'type': 'instantaneous', 'camera_id_start': 1, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 18, 20), 'timestamp_end': None, 'measured_speed': 151.4}, {'violation_id': '658b0651-f3aa-4e9d-87ea-84ba4671a0df', 'type': 'instantaneous', 'camera_id_start': 2, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 18, 45, 771000), 'timestamp_end': None, 'measured_speed': 141.8}, {'violation_id': '13c97a12-7a3c-420e-9d9c-e83b389c65f7', 'type': 'average', 'camera_id_start': 1, 'camera_id_end': 2, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 18, 20), 'timestamp_end': datetime.datetime(2024, 1, 1, 16, 18, 45, 771000), 'measured_speed': 146.60000000000002}, {'violation_id': 'efd127e8-e6d0-4741-bbf2-381c8abd80ce', 'type':

✅ Sent to Kafka (mongo_plot_stream): {'_id': ObjectId('6836ed8cc81318e00db4b428'), 'car_plate': 'SI 61', 'date': datetime.datetime(2024, 1, 1, 0, 0), 'violations': [{'violation_id': 'f1eb0747-85bf-4637-a31f-a02d1496ae82', 'type': 'instantaneous', 'camera_id_start': 1, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 18, 20), 'timestamp_end': None, 'measured_speed': 151.4}, {'violation_id': '658b0651-f3aa-4e9d-87ea-84ba4671a0df', 'type': 'instantaneous', 'camera_id_start': 2, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 18, 45, 771000), 'timestamp_end': None, 'measured_speed': 141.8}, {'violation_id': '13c97a12-7a3c-420e-9d9c-e83b389c65f7', 'type': 'average', 'camera_id_start': 1, 'camera_id_end': 2, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 18, 20), 'timestamp_end': datetime.datetime(2024, 1, 1, 16, 18, 45, 771000), 'measured_speed': 146.60000000000002}, {'violation_id': 'efd127e8-e6d0-4741-bbf2-381c8abd80ce', 'type':

✅ Sent to Kafka (mongo_plot_stream): {'_id': ObjectId('6836ededc81318e00db4b4d6'), 'car_plate': 'QKR 18', 'date': datetime.datetime(2024, 1, 1, 0, 0), 'violations': [{'violation_id': '6d6a0fdd-4f72-445f-9ab3-ba865d31b869', 'type': 'instantaneous', 'camera_id_start': 1, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 18, 17), 'timestamp_end': None, 'measured_speed': 127.7}, {'violation_id': 'a8732b21-216e-4fe4-aad5-9665fca7230c', 'type': 'instantaneous', 'camera_id_start': 2, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 18, 45, 490000), 'timestamp_end': None, 'measured_speed': 120.8}, {'violation_id': 'b6a4cd2b-cf07-43cc-af0f-38b1376e6015', 'type': 'average', 'camera_id_start': 1, 'camera_id_end': 2, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 18, 17), 'timestamp_end': datetime.datetime(2024, 1, 1, 16, 18, 45, 490000), 'measured_speed': 124.25}, {'violation_id': '798a6372-aa33-4ab2-b123-3f0534b982a6', 'type': 'instantan

✅ Sent to Kafka (mongo_plot_stream): {'_id': ObjectId('6836ededc81318e00db4b4e0'), 'car_plate': 'APU 41', 'date': datetime.datetime(2024, 1, 1, 0, 0), 'violations': [{'violation_id': '0e3ef893-18aa-4dee-9093-12bfa3516a86', 'type': 'instantaneous', 'camera_id_start': 1, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 34, 30), 'timestamp_end': None, 'measured_speed': 158.4}, {'violation_id': '3b2f9d73-15ec-4e5f-bd48-d8cd96efd185', 'type': 'instantaneous', 'camera_id_start': 2, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 34, 52, 109000), 'timestamp_end': None, 'measured_speed': 158.5}, {'violation_id': 'ac73538c-2a49-4fdf-b227-cc06dd3c638c', 'type': 'average', 'camera_id_start': 1, 'camera_id_end': 2, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 34, 30), 'timestamp_end': datetime.datetime(2024, 1, 1, 16, 34, 52, 109000), 'measured_speed': 158.45}, {'violation_id': 'a876d7a6-9bc1-43b0-8e8a-4f3c03799dae', 'type': 'instantan

✅ Sent to Kafka (mongo_plot_stream): {'_id': ObjectId('6836ededc81318e00db4b4e0'), 'car_plate': 'APU 41', 'date': datetime.datetime(2024, 1, 1, 0, 0), 'violations': [{'violation_id': '0e3ef893-18aa-4dee-9093-12bfa3516a86', 'type': 'instantaneous', 'camera_id_start': 1, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 34, 30), 'timestamp_end': None, 'measured_speed': 158.4}, {'violation_id': '3b2f9d73-15ec-4e5f-bd48-d8cd96efd185', 'type': 'instantaneous', 'camera_id_start': 2, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 34, 52, 109000), 'timestamp_end': None, 'measured_speed': 158.5}, {'violation_id': 'ac73538c-2a49-4fdf-b227-cc06dd3c638c', 'type': 'average', 'camera_id_start': 1, 'camera_id_end': 2, 'timestamp_start': datetime.datetime(2024, 1, 1, 16, 34, 30), 'timestamp_end': datetime.datetime(2024, 1, 1, 16, 34, 52, 109000), 'measured_speed': 158.45}, {'violation_id': 'a876d7a6-9bc1-43b0-8e8a-4f3c03799dae', 'type': 'instantan